<img src="https://www.allianz.com/content/dam/onemarketing/system/AZ_Logo_Twitter_438x220px.png" width=450>

# Outlook and Commentary

### import Libraries

In [88]:
import requests
from bs4 import BeautifulSoup

from selenium.webdriver.common.action_chains import ActionChains
from time import sleep
import selenium
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.common.by import By
from selenium.webdriver.support import expected_conditions as EC
import json
import re
from pprint import pprint
from tqdm import tqdm
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.service import Service
from webdriver_manager.chrome import ChromeDriverManager
import datetime
from datetime import timedelta

### Outlook and Commentary URL

In [82]:
outlook_and_commentary_url = 'https://www.allianzgi.com/en/insights/outlook-and-commentary'
main_china_url = 'https://www.allianzgi.com/en/investable-themes/china/china-insights'

In [83]:
driver = webdriver.Chrome()
driver.get(outlook_and_commentary_url)
sleep(5)
driver.find_element(By.CSS_SELECTOR, '#onetrust-accept-btn-handler').click()
# driver.implicitly_wait(5)
while True:

    try:
        show_more_button = driver.find_element(By.CSS_SELECTOR, 'body > main > div > div > div.l-grid__row.align-items-stretch.js-list-view-container > div.u-flex.justify-content-center.u-margin-top-2m.show-more-center > a')    
        driver.execute_script("arguments[0].click();", show_more_button)

    except: 
        break
        
    finally:
        links = [i.get_attribute('href') for i in driver.find_elements(By.CSS_SELECTOR, "[class='l-grid u-padding-top-xl u-padding-bottom-xl js-list-view c-list-view'] [class='c-heading__link']")]
        title_list = [i.text for i in driver.find_elements(By.CSS_SELECTOR,"[class='l-grid__row align-items-stretch js-list-view-container'] a[class='c-heading__link']")]
        date_list = [i.text for i in driver.find_elements(By.CSS_SELECTOR,"[class='l-grid u-padding-top-xl u-padding-bottom-xl js-list-view c-list-view'] [class='c-agi-tile__footer']")]
        abstract_list = [i.text for i in driver.find_elements(By.CSS_SELECTOR, "[class='l-grid u-padding-top-xl u-padding-bottom-xl js-list-view c-list-view'] [class='c-copy c-agi-tile__text']")]
        
driver.quit()

In [91]:
def to_date_format(raw_date):
    
    format_1 = re.findall(r'\b\d+\sdays ago\b',raw_date)
    format_2 = re.findall(r'\d+/\d+/\d+',raw_date)
    
    if bool(format_1) is True:
        n = int(''.join(re.findall(r'\d+',''.join(format_1))))
        extract_date = datetime.date.today() - timedelta(days=n)
        date = f'{extract_date.day}/{extract_date.month}/{extract_date.year}'
        return date
    
    elif bool(format_2) is True:
        date = ''.join(format_2)
        return date
    
    else:
        date = 'N/A'
        return date

In [92]:
def extract_content(link):
    
    # Send requrst and create BeautifulSoup object
    response = requests.get(link)
    soup = BeautifulSoup(response.text)
    
     # Tag
    tag = soup.find_all(class_='c-copy u-margin-bottom-none u-text-center u-margin-bottom-2xs')
    if bool(tag) is True: 
        tag = tag[0].text.strip()
    else:
        tag = 'N/A'
    
    # Content
    raw_content = soup.find_all(class_ = 'l-container l-container--no-gutters')
    
    if bool(soup.find_all(class_ = 'l-container l-container--no-gutters')) is True: 
        raw_content = ' '.join([i.text for i in raw_content])
        content = re.sub('\s+',' ', raw_content)
    else:
        content = 'N/A' 
    
    return content, tag

In [93]:
list_of_dict = []
index = 1

for title, date, link, abstract in tqdm(zip(title_list, date_list, links, abstract_list)):
    d = {'index': index,
         'company': 'Allianz', 
         'topic': 'Insight', 
         'insight_topic': 'Outlook & commentary',
         'title': title,
         'date': to_date_format(date),
         'link': link,
         'tag': extract_content(link=link)[1],
         'abstract': abstract,
         'content': extract_content(link=link)[0]
        }
    
    list_of_dict.append(d)
    index += 1

206it [11:40,  3.40s/it]


In [97]:
list_of_dict

[{'index': 1,
  'company': 'Allianz',
  'topic': 'Insight',
  'insight_topic': 'Outlook & commentary',
  'title': 'How China can achieve its ambitious decarbonisation plan',
  'date': '22/8/2022',
  'link': 'https://www.allianzgi.com/en/home/insights/outlook-and-commentary/ambitious-decarbonisation-plan',
  'tag': 'Appreciating China',
  'abstract': 'China’s pledge to achieve net-zero by 2060 appears ambitious, but it is central to the country’s broader strategic interests and the pathway to realising its goal could provide new opportunities for investors.',
  'content': ' Appreciating China How China can achieve its ambitious decarbonisation plan Virginie Maisonneuve | Shannon Zheng 8/22/2022 Share on Facebook Share on LinkedIn Share on Twitter Share via email China’s pledge to achieve net-zero by 2060 appears ambitious, but it is central to the country’s broader strategic interests and the pathway to realising its goal could provide new opportunities for investors. Key takeaways Chin

# Appreciating China - China insights

In [41]:
main_china_url = 'https://www.allianzgi.com/en/investable-themes/china/china-insights'

In [75]:
def extract_article_links(main_china_url):

    chrome_options = Options()
    chrome_options.add_argument("--no-sandbox")
    chrome_options.add_argument("--headless")
    chrome_options.add_argument("start-maximized")
    chrome_options.add_experimental_option("excludeSwitches", ["enable-automation"])
    chrome_options.add_experimental_option('useAutomationExtension', False)
    #webdriver_service = Service(executable_path=ChromeDriverManager().install())
    driver = webdriver.Chrome(options=chrome_options)


    driver.get(main_china_url)
    sleep(5)

    cookies_button = driver.find_element(By.ID, 'onetrust-accept-btn-handler')
    cookies_button.click()

    
    for i in range(2):
        loadmore_button = driver.find_element(By.XPATH, '/html/body/main/div[1]/div/div[4]/div[10]/a')
        loadmore_button.click()

    sleep(3)
    links_list = [link.get_attribute('href') for link in driver.find_elements(By.XPATH, "//div[@class='c-agi-tile__content']//a[@aria-label='Discover more']")]
    abstract_list = [i.text for i in driver.find_elements(By.CSS_SELECTOR, "[class='l-grid u-padding-top-xl u-padding-bottom-xl js-list-view c-list-view'] [class='c-copy c-agi-tile__text']")]
    return links_list, abstract_list


In [76]:
def extract_allianz_china_insight(article_china_url):

    r = requests.get(article_china_url)
    soup = BeautifulSoup(r.text)
    
    title = soup.find('h1').text.strip()
    raw_date = soup.find(class_='c-copy u-margin-bottom-none').text.strip()
    date = ''.join(i for i in re.findall(r'\d+/\d+/\d+', raw_date))
    raw_content = soup.find(class_='l-container l-container--no-gutters').text.strip()
    content = re.sub(r'\s+',' ', raw_content)
    
    return {
            'index': '',
            'Company': 'Allianz',
            'Topic': 'Insight',
            'insight_topic': 'Appreciating China',
            'title': title,
            'date': date,
            'link': article_china_url,
            'tag': '',
            'abstract': '',
            'content': content,
    }

In [77]:
all_china_links = extract_article_links('https://www.allianzgi.com/en/investable-themes/china/china-insights')[0]
all_abstract_list = extract_article_links('https://www.allianzgi.com/en/investable-themes/china/china-insights')[1]

In [79]:
all_china_links

['https://www.allianzgi.com/en/home/investable-themes/china/china-insights/will-chinas-markets-roar-again-in-the-year-of-the-tiger',
 'https://www.allianzgi.com/en/home/investable-themes/china/china-insights/chinas-rmb-bond-market',
 'https://www.allianzgi.com/en/home/investable-themes/china/china-insights/using-ai-to-discover-asias-environmental-leaders',
 'https://www.allianzgi.com/en/home/investable-themes/china/china-insights/nine-themes-for-investing-in-chinas-transformation',
 'https://www.allianzgi.com/en/home/investable-themes/china/china-insights/chinas-2060-net-zero-carbon-goal',
 'https://www.allianzgi.com/en/home/investable-themes/china/china-insights/chinas-phase-3',
 'https://www.allianzgi.com/en/home/investable-themes/china/china-insights/7-reasons-to-stay-invested-in-china-equities',
 'https://www.allianzgi.com/en/home/investable-themes/china/china-insights/9-things-to-know-about-china-bond-markets',
 'https://www.allianzgi.com/en/home/investable-themes/china/china-insi

In [80]:
allianz_china_insight_list = []

index = 1
for link,abstract in zip(all_china_links, all_abstract_list):
    allianz_insight_dict = extract_allianz_china_insight(link)
    allianz_insight_dict['index'] = index
    allianz_insight_dict['abstract'] = abstract
    allianz_china_insight_list.append(allianz_insight_dict)
    index += 1

In [65]:
allianz_china_insight_list

[{'index': 1,
  'Company': 'Allianz',
  'Topic': 'China Insight',
  'title': 'Following recent volatility, will China’s markets roar again in the Year of the Tiger?',
  'date': '26/01/2022',
  'link': 'https://www.allianzgi.com/en/home/investable-themes/china/china-insights/will-chinas-markets-roar-again-in-the-year-of-the-tiger',
  'content': 'Following recent volatility, will China’s markets roar again in the Year of the Tiger? 26/01/2022 Share on twitter Share on LinkedIn Share on facebook Share via email Summary Recent market turbulence in China may have attracted attention, but the country’s transformation story is far from over. The Year of the Tiger could offer multiple opportunities for investors, notably around sectors related to China’s future technologies and climate programmes. Key takeaways Volatility is a part of China’s investment story – as 2021 demonstrated – but the country’s development trajectory remains promising as we enter the Year of the Tiger Continued focus on

In [81]:
from itertools import chain

In [99]:
all_inshits = list(chain(list_of_dict,allianz_china_insight_list))

In [100]:
index = 1
for dict_ in all_inshits:
    dict_['index'] = index
    index += 1

In [101]:
all_inshits

[{'index': 1,
  'company': 'Allianz',
  'topic': 'Insight',
  'insight_topic': 'Outlook & commentary',
  'title': 'How China can achieve its ambitious decarbonisation plan',
  'date': '22/8/2022',
  'link': 'https://www.allianzgi.com/en/home/insights/outlook-and-commentary/ambitious-decarbonisation-plan',
  'tag': 'Appreciating China',
  'abstract': 'China’s pledge to achieve net-zero by 2060 appears ambitious, but it is central to the country’s broader strategic interests and the pathway to realising its goal could provide new opportunities for investors.',
  'content': ' Appreciating China How China can achieve its ambitious decarbonisation plan Virginie Maisonneuve | Shannon Zheng 8/22/2022 Share on Facebook Share on LinkedIn Share on Twitter Share via email China’s pledge to achieve net-zero by 2060 appears ambitious, but it is central to the country’s broader strategic interests and the pathway to realising its goal could provide new opportunities for investors. Key takeaways Chin

In [103]:
with open('allianz-inshits.json', 'w') as f:
    json.dump(all_inshits , f, indent=4 )